# Mean Teacher Bert Assessment



# Requirement Installation 

In [59]:
#installing requirements
!pip install tensorflow_text
!pip install textattack
!pip install sentence_transformers

  Using cached importlib_metadata-4.8.2-py3-none-any.whl (17 kB)
  Attempting uninstall: importlib-metadata
    Found existing installation: importlib-metadata 3.10.1
    Uninstalling importlib-metadata-3.10.1:
      Successfully uninstalled importlib-metadata-3.10.1
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
konoha 4.6.5 requires importlib-metadata<4.0.0,>=3.7.0, but you have importlib-metadata 4.8.2 which is incompatible.


  Using cached importlib_metadata-3.10.1-py3-none-any.whl (14 kB)
  Attempting uninstall: importlib-metadata
    Found existing installation: importlib-metadata 4.8.2
    Uninstalling importlib-metadata-4.8.2:
      Successfully uninstalled importlib-metadata-4.8.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
markdown 3.3.6 requires importlib-metadata>=4.4; python_version < "3.10", but you have importlib-metadata 3.10.1 which is incompatible.



# Importing and Declaration

In [60]:
import os 
os.chdir('/content/drive/MyDrive/Master Thesis/Mean-Teacher-BERT-Robustness-Assessment/')

In [61]:
# importing libraries 
import os 
import datetime

import pandas as pd 
import numpy as np
import tensorflow as tf

from ipywidgets import *
from IPython.display import display


from Utils.utils import label_to_int, dataset_split, convert_to_category, create_tokenizer, data_tokenization
from Utils.data_loader import data_loader
from Bert.bert_model import bert_model



from MeanTeacher.train_mean_teacher import train_mean_teacher

from sklearn.metrics import classification_report

import random 
random.seed(42)

## Data Related Questionaire

In [62]:
data_name=widgets.Dropdown(options=['codalab','IMDB' ],value='codalab',description='DATA:',disabled=False,) 
pretrained_weights=widgets.Dropdown(options=['bert-base-uncased','distilbert-base-uncased' ],value='bert-base-uncased',description='Pretrained Model:',disabled=False,)
widgets.HBox([data_name, pretrained_weights])

### Data specific detail

In [63]:
'''
NOT required now as previous cell does the job. So disabling boxes
'''
# Details related to the dataset
# columns names 
feature_col=widgets.Text(value='tweet',placeholder='Enter Feature Col Name',description='Feature Column:',disabled=False)
target_col=widgets.Text(value='label',placeholder='Enter Target Col Name',description='Target Column:',disabled=False) 
aug_col=widgets.Text(value='aug_tweet',placeholder='Enter Augmented data Col Name',description='Augment Column:',disabled=False)   

#pretrained model details
 # widgets.HBox([feature_col,target_col,aug_col,pretrained_weights])

In [64]:
#details of the class
class_1=widgets.Text(value='real',placeholder='Enter class name 1',description='class 1:',disabled=False)
class_2=widgets.Text(value='fake',placeholder='Enter class name 2',description='class 2:',disabled=False) 
tf.print("Class 1 label would be 0. \n")
# widgets.HBox([class_1,class_2])

Class 1 label would be 0. 



In [65]:
# #Data location 
Data_loc=widgets.Text(value='Data/codalab/',placeholder='Enter Data location ',description=' Data Location Column:',disabled=False)   
# widgets.HBox([Data_loc])

In [66]:
'''
Adjusting feature as per data 
'''

if data_name.value=='codalab':
    feature_col.value='tweet'
    target_col.value='label'
    aug_col.value='aug_tweet'
    class_1.value='real'
    class_2.value='fake'
    Data_loc.value= 'Data/codalab/'
elif data_name.value=='IMDB':
    feature_col.value='review'
    target_col.value='sentiment'
    aug_col.value='aug_tweet'
    class_1.value='positive'
    class_2.value='negative'
    Data_loc.value= 'Data/IMDB/'



## Hyperparameter selections

In [67]:
# Parameter declaration 
max_len=widgets.BoundedIntText(value=100,min=10,max=512,step=10,description='Max Length:',disabled=False,)

learning_rate= widgets.Dropdown(options=[2e-5, 1e-5, 1e-3],value=2e-5,description='Learning Rate:',disabled=False,)

epochs= widgets.Dropdown(options=[3, 4, 5,6],value=3,description='Epochs:',disabled=False,)

batch_size= widgets.Dropdown(options=[4, 5,6,7,8],value=4,description='Batch Size:',disabled=False,)

#for mean teacher model
alpha= widgets.BoundedFloatText(value=0.999,min=0.90,max=0.999,step=0.0001,description='Alpha:',disabled=False, readout_format='.3f')
ratio= widgets.BoundedFloatText(value=0.5,min=0.1,max=0.9,step=0.1,description='Ratio:',disabled=False, readout_format='.2f')
# pretrained_weights=widgets.Dropdown(options=['bert-base-uncased','distilbert-base-uncased' ],value='bert-base-uncased',description='Pretrained Model:',disabled=False,)

tf.print('\n Max Length: Length of the article')
display(max_len)
tf.print('\n Learning rate: Learning rate for training the model')
display(learning_rate)
tf.print('\n Epochs')
display(epochs)
tf.print('\n batch_size')
display(batch_size)
tf.print('\n Alpha: Parameter related to Mean teacher model, its the proportion of student weight that teacher model will get each step.')
display(alpha)
tf.print("\n Ratio: Parameter related to Mean Teacher model, that manage the proportion of classification cost and consistency cost in calculating overall cost.")
display(ratio)

# widgets.HBox([max_len, learning_rate, epochs, batch_size,alpha,ratio])


 Max Length: Length of the article


BoundedIntText(value=100, description='Max Length:', max=512, min=10, step=10)


 Learning rate: Learning rate for training the model


Dropdown(description='Learning Rate:', options=(2e-05, 1e-05, 0.001), value=2e-05)


 Epochs


...

Dropdown(description='Batch Size:', options=(4, 5, 6, 7, 8), value=4)


 Alpha: Parameter related to Mean teacher model, its the proportion of student weight that teacher model will get each step.


BoundedFloatText(value=0.999, description='Alpha:', max=0.999, min=0.9, step=0.0001)


 Ratio: Parameter related to Mean Teacher model, that manage the proportion of classification cost and consistency cost in calculating overall cost.


BoundedFloatText(value=0.5, description='Ratio:', max=0.9, min=0.1, step=0.1)

# Reading dataset

In [68]:
df_train,df_test,df_aug_unlabel= data_loader(Data_loc.value,target_col.value,aug_col.value,class_1.value)

In [69]:
len(df_train),len(df_test)

(6090, 2040)

In [70]:
tf.print(df_train.groupby(target_col.value).count())
tf.print(df_test.groupby(target_col.value).count())

       tweet
label       
0       3199
1       2891
       tweet
label       
0       1071
1        969


# Training 

<font color='blue'>This section is to train and save the model. <br>
__If model is already trained and saved, directly move forward for attack and evaluation section.__ </font>

## BERT Model Training (Baseline)

In [ ]:
pretrained_weights.value

'distilbert-base-uncased'

In [ ]:
tokenizer=create_tokenizer(pretrained_weights.value)
x_train,y_train,vocab_size= data_tokenization(df_train,feature_col.value,target_col.value,max_len.value,tokenizer)
x_test,y_test,_= data_tokenization(df_test,feature_col.value,target_col.value,max_len.value,tokenizer)

In [ ]:
#printing hyperparameters set for training 
print(f'Alpha: {alpha.value}, Max len : {max_len.value}, Learning Rate: {learning_rate.value}, Batch Size: {batch_size.value}, Ratio: {ratio.value}, Epochs: {epochs.value}')

Alpha: 0.999, Max len : 100, Learning Rate: 2e-05, Batch Size: 4, Ratio: 0.5, Epochs: 3


In [ ]:
bert=bert_model(pretrained_weights.value,max_len.value,learning_rate.value)
bert.summary()

Model selected: distilbert-base-uncased


Some layers from the model checkpoint at distilbert-base-uncased were not used when initializing TFDistilBertModel: ['vocab_layer_norm', 'vocab_transform', 'vocab_projector', 'activation_13']
- This IS expected if you are initializing TFDistilBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFDistilBertModel were initialized from the model checkpoint at distilbert-base-uncased.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFDistilBertModel for predictions without further training.


Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_ids (InputLayer)         [(None, 100)]        0           []                               
                                                                                                  
 attention_mask (InputLayer)    [(None, 100)]        0           []                               
                                                                                                  
 tf_distil_bert_model (TFDistil  TFBaseModelOutput(l  66362880   ['input_ids[0][0]',              
 BertModel)                     ast_hidden_state=(N               'attention_mask[0][0]']         
                                one, 100, 768),                                                   
                                 hidden_states=None                                           

In [ ]:
print(datetime.datetime.now())
with tf.device('/GPU:0'):
    bert.fit(x_train,y_train,batch_size=batch_size.value,epochs=epochs.value,verbose=1)

2021-11-27 10:53:40.537232
Epoch 1/3


KeyboardInterrupt: ignored

In [ ]:
# evaluating model 
pred_label=bert.predict(x_test)

print(classification_report(np.argmax(y_test,1),np.argmax(pred_label,1)))

In [ ]:
#saving the model 
if  pretrained_weights.value == 'distilbert-base-uncased':
    bert.save_weights('SavedModels/'+data_name.value+'/DistilBERT_model.h5')
else:
    bert.save_weights('SavedModels/'+data_name.value+'/BERT_model.h5')

## Adversarial Mean Teacher BERT Training(Proposed)

In [ ]:
# Training
tokenizer=create_tokenizer(pretrained_weights.value)
x_train,y_train,vocab_size= data_tokenization(df_train,feature_col.value,target_col.value,max_len.value,tokenizer)
x_test,y_test,_= data_tokenization(df_test,feature_col.value,target_col.value,max_len.value,tokenizer)
x_unlabel,_,_=data_tokenization(df_aug_unlabel,aug_col.value,target_col.value,max_len.value,tokenizer)

In [ ]:
#printing hyperparameters set for training 
print(f'Alpha: {alpha.value}, Max len : {max_len.value}, Learning Rate: {learning_rate.value}, Batch Size: {batch_size.value}, Ratio: {ratio.value}, Epochs: {epochs.value}')


In [ ]:
print(datetime.datetime.now())
# training the model
with tf.device('/GPU:0'):
    student, teacher= train_mean_teacher(x_train, y_train, x_unlabel, 
                                         pretrained_weights.value,
                                         epochs.value,batch_size.value,
                                         learning_rate.value,max_len.value,alpha.value)

In [ ]:
if  pretrained_weights.value == 'distilbert-base-uncased':
    teacher.save_weights('SavedModels/'+data_name.value+'/DistilBERT_teacher.h5')
else:
    teacher.save_weights('SavedModels/'+data_name.value+'/BERT_teacher.h5')


In [ ]:
#evaluating test data 
pred_label=teacher.predict(x_test)

In [ ]:
print(classification_report(np.argmax(y_test,1),np.argmax(pred_label,1)))

# Attack And Evaluation

In [71]:
import textattack
from Attack_model.TextAttack import attack_model

In [72]:
# bert_to_attack=widgets.Textarea(value='SavedModels/Codalab/BERT_model.h5',placeholder='Enter Model location ',description=' BERT Model location:',disabled=False)
# MTbert_to_attack=widgets.Textarea(value='SavedModels/Codalab/BERT_teacher.h5',placeholder='Enter Model location ',description=' MTBERT Model location:',disabled=False)   
# pretrained_weights=widgets.Dropdown(options=['bert-base-uncased','distilbert-base-uncased' ],value='bert-base-uncased',description='Pretrained Model:',disabled=False,) 
model_name=widgets.Dropdown(options=['BERT','DistilBERT']
                               ,value='BERT',
                               description='Model Name:',
                               disabled=False,) 
tf.print('\n model_name: Model name for attack.Note : Please confirm with the bert_to_attack parameter')
display(model_name)

# tf.print('\n Please select the location of BERT and MT BERT model.\n')
# display(bert_to_attack, MTbert_to_attack)
# tf.print('\n Please select the pretrained model weights.')
# display(pretrained_weights)



 model_name: Model name for attack.Note : Please confirm with the bert_to_attack parameter


Dropdown(description='Model Name:', options=('BERT', 'DistilBERT'), value='BERT')

In [73]:
if model_name.value=='BERT':
  bert_to_attack= 'SavedModels/'+data_name.value+'/BERT_model.h5'
  MTbert_to_attack='SavedModels/'+data_name.value+'/BERT_teacher.h5'
  pretrained_weights.value = 'bert-base-uncased'
else:
  bert_to_attack= 'SavedModels/'+data_name.value+'/DistilBERT_model.h5'
  MTbert_to_attack='SavedModels/'+data_name.value+'/DistilBERT_teacher.h5'
  pretrained_weights.value = 'distilbert-base-uncased'
print(model_name.value), bert_to_attack

BERT


(None, 'SavedModels/codalab/BERT_model.h5')

In [74]:
# attack parameters 

# Query Budget is maximum query allowed
query_budget= widgets.BoundedIntText(value=6000,min=10,max=10000,step=20,description='Query Budget:',disabled=False,)

# number of example to take for attack from test dataset randomly 
num_examples=widgets.BoundedIntText(value=1000,min=10,max=len(df_test),step=20,description='Number of Example:',disabled=False,)

# attack recipes 
attack_recipe=widgets.Dropdown(options=['TextFoolerJin2019',
                                        'PWWSRen2019',
                                        'BAEGarg2019',
                                        'TextBuggerLi2018']
                               ,value='TextFoolerJin2019',
                               description='Attack Recipe:',
                               disabled=False,) 


tf.print('\n query_budget: Maximum Query allowed to attack model')
display(query_budget)
tf.print('\n num_examples: Number of example to take for attack from test dataset randomly. ')
display(num_examples)
# tf.print('\n attack_recipe: Attack methodolgy to attack the model. ')
# display(attack_recipe)



 query_budget: Maximum Query allowed to attack model


BoundedIntText(value=6000, description='Query Budget:', max=10000, min=10, step=20)


 num_examples: Number of example to take for attack from test dataset randomly. 


BoundedIntText(value=1000, description='Number of Example:', max=2040, min=10, step=20)

In [75]:
'''
Some of the attack recipe provided by textattack is not working with lengthy article. So, 
I am filtering the with the length. May be in future I will remove it.
'''
if not os.path.exists('Data/'+data_name.value+'/AdversarialTestData/test_adv_'+str(num_examples.value)+'.csv'):
    df_test['len']=df_test.apply(lambda row: len(row[feature_col.value].split()),axis=1)
    print(f'Average length of articles are: {df_test["len"].mean()}')
    # df_test_for_attack= df_test[(df_test['len']>0) & (df_test['len']<100)][[feature_col.value,target_col.value]].dropna().reset_index(drop=True)
    df_test_for_attack=df_test[[feature_col.value,target_col.value]].sample(frac=1).reset_index(drop=True)
    df_test_for_attack= df_test_for_attack[:num_examples.value+1]
    # saving the csv file in AdversarialTestData folder, in order to correctly experiment all recipes with same data
    df_test_for_attack.to_csv('Data/'+data_name.value+'/AdversarialTestData/test_adv_'+str(num_examples.value)+'.csv',index=False)
else:
    tf.print('Reading the saved file')
    df_test_for_attack= pd.read_csv('Data/'+data_name.value+'/AdversarialTestData/test_adv_'+str(num_examples.value)+'.csv')

print('Length of dataset', len(df_test_for_attack))
df_test_for_attack.head()

Reading the saved file
Length of dataset 1001


tweet  label
0  back in march former deputy prime minister bar...      1
1  covid is a lab made biological weapon deployed...      1
2  indiafightscorona by conducting close to crore...      0
3  claim that saint corona ha always been a patro...      1
4  million people contracted tuberculosis last ye...      1

In [76]:
df_test_for_attack.groupby(target_col.value).count()

tweet
label       
0        530
1        471

In [77]:

#creating dataset for the attacking
dataset_for_attack=list(df_test_for_attack.itertuples(index=False, name=None))
dataset_for_attack = textattack.datasets.Dataset(dataset_for_attack)

In [78]:
# Loading the model
bert= bert_model(pretrained_weights.value,max_len.value,learning_rate.value) 
bert.load_weights(bert_to_attack)

bert_teacher= bert_model(pretrained_weights.value,max_len.value,learning_rate.value) 
bert_teacher.load_weights(MTbert_to_attack)

Model selected: bert-base-uncased


Some layers from the model checkpoint at bert-base-uncased were not used when initializing TFBertModel: ['mlm___cls', 'nsp___cls']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFBertModel were initialized from the model checkpoint at bert-base-uncased.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


Model selected: bert-base-uncased


Some layers from the model checkpoint at bert-base-uncased were not used when initializing TFBertModel: ['mlm___cls', 'nsp___cls']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFBertModel were initialized from the model checkpoint at bert-base-uncased.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


### TextFooler
__TextFoolerJin2019 - Is BERT Really Robust? A Strong Baseline for Natural Language Attack on Text Classification and Entailment.__<br>
In this paper, we present TextFooler, a simple but strong baseline to generate natural adversarial text. By applying it to two fundamental natural language tasks, text classification and textual entailment, we successfully attacked three target models, including the powerful pre-trained BERT, and the widely used convolutional and recurrent neural networks. We demonstrate the advantages of this framework in three ways: (1) effective---it outperforms state-of-the-art attacks in terms of success rate and perturbation rate, (2) utility-preserving---it preserves semantic content and grammaticality, and remains correctly classified by humans, and (3) efficient---it generates adversarial text with computational complexity linear to the text length. *The code, pre-trained target models, and test examples are available at https://github.com/jind11/TextFooler.


In [79]:
attack_recipe.value= 'TextFoolerJin2019'
tf.print(f'****Attack Recipe:{attack_recipe.value}*****')
tf.print(f'****Query size:{query_budget.value}*****')
tf.print(f'****Number of examples:{num_examples.value}*****')
tf.print(f'****Attacking model :{model_name.value}*****')

****Attack Recipe:TextFoolerJin2019*****
****Query size:6000*****
****Number of examples:1000*****
****Attacking model :BERT*****


#### BERT

In [80]:
attack_model(bert, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/TextFoolerJin2019/BERT_nexp1000_qb6000_2021-12-06_01:52.csv

  0%|          | 0/1000 [00:00<?, ?it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.840845057
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
       


  0%|          | 1/1000 [00:05<1:24:45,  5.09s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 1/1000 [00:05<1:24:56,  5.10s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[1 (73%)]] --> [[0 (53%)]]

back in march former deputy [[prime]] minister barnabyjoyce [[said]] [[death]] by [[snake]] [[bite]] outnumbered covid death by a factor of to but coronavirus move quickly and his claim rapidly aged this and more in coronacheck coronavirusfacts

back in march former deputy [[frst]] minister barnabyjoyce [[submits]] [[casualties]] by [[vipers]] [[mouthful]] outnumbered covid death by a factor of to but coronavirus move quickly and his claim rapidly aged this and more in coronacheck coronavirusfacts





[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 2/1000 [00:08<1:11:11,  4.28s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   0%|          | 2/1000 [00:08<1:11:17,  4.29s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[0 (73%)]] --> [[1 (52%)]]

[[looking]] at the [[case]] [[data]] there is now a [[fairly]] clear low plateau where the day [[average]] [[stayed]] between k [[case]] per [[day]] this [[extended]] from to [[so]] from ago to day ago

[[researches]] at the [[matter]] [[indications]] there is now a [[perfectly]] clear low plateau where the day [[medial]] [[suspended]] between k [[phenomenon]] per [[stardate]] this [[lange]] from to [[why]] from ago to day ago





[Succeeded / Failed / Skipped / Total] 865 / 75 / 58 / 998: 100%|█████████▉| 999/1000 [26:26<00:01,  1.59s/it]
[Succeeded / Failed / Skipped / Total] 866 / 75 / 58 / 999: 100%|█████████▉| 999/1000 [26:26<00:01,  1.59s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (73%)]] --> [[1 (50%)]]

arizona [[put]] out a somewhat [[encouraging]] set of number unclear if this is the [[beginning]] of a real downward [[trend]] or just some bump on an upward trajectory

arizona [[made]] out a somewhat [[motivator]] set of number unclear if this is the [[starting]] of a real downward [[slanted]] or just some bump on an upward trajectory





[Succeeded / Failed / Skipped / Total] 866 / 75 / 58 / 999: 100%|██████████| 1000/1000 [26:27<00:00,  1.59s/it]
[Succeeded / Failed / Skipped / Total] 867 / 75 / 58 / 1000: 100%|██████████| 1000/1000 [26:27<00:00,  1.59s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[1 (73%)]] --> [[0 (56%)]]

the [[novel]] coronavirus ncov will not last long in the philippine because of it warm climate

the [[latest]] coronavirus ncov will not last long in the philippine because of it warm climate



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 867    |
| Number of failed attacks:     | 75     |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 94.2%  |
| Accuracy under attack:        | 7.5%   |
| Attack success rate:          | 92.04% |
| Average perturbed word %:     | 22.69% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 183.59 |
+-------------------------------+--------+


#### MT BERT

In [81]:
attack_model(bert_teacher, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             'MT'+model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/TextFoolerJin2019/MTBERT_nexp1000_qb6000_2021-12-06_02:18.csv

  0%|          | 0/1000 [00:00<?, ?it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.840845057
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
       


  0%|          | 1/1000 [00:07<1:59:26,  7.17s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|          | 1/1000 [00:07<1:59:37,  7.19s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[1 (60%)]] --> [[[FAILED]]]

back in march former deputy prime minister barnabyjoyce said death by snake bite outnumbered covid death by a factor of to but coronavirus move quickly and his claim rapidly aged this and more in coronacheck coronavirusfacts





[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|          | 2/1000 [00:14<1:57:58,  7.09s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   0%|          | 2/1000 [00:14<1:58:03,  7.10s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[0 (63%)]] --> [[[FAILED]]]

looking at the case data there is now a fairly clear low plateau where the day average stayed between k case per day this extended from to so from ago to day ago





[Succeeded / Failed / Skipped / Total] 417 / 536 / 45 / 998: 100%|█████████▉| 999/1000 [40:41<00:02,  2.44s/it]
[Succeeded / Failed / Skipped / Total] 418 / 536 / 45 / 999: 100%|█████████▉| 999/1000 [40:41<00:02,  2.44s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (61%)]] --> [[1 (53%)]]

arizona put out a somewhat [[encouraging]] set of [[number]] unclear if this is the [[beginning]] of a real [[downward]] trend or just some bump on an [[upward]] trajectory

arizona put out a somewhat [[inspirational]] set of [[numerals]] unclear if this is the [[principle]] of a real [[downsized]] trend or just some bump on an [[climbs]] trajectory





[Succeeded / Failed / Skipped / Total] 418 / 536 / 45 / 999: 100%|██████████| 1000/1000 [40:43<00:00,  2.44s/it]
[Succeeded / Failed / Skipped / Total] 418 / 537 / 45 / 1000: 100%|██████████| 1000/1000 [40:43<00:00,  2.44s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[1 (61%)]] --> [[[FAILED]]]

the novel coronavirus ncov will not last long in the philippine because of it warm climate



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 418    |
| Number of failed attacks:     | 537    |
| Number of skipped attacks:    | 45     |
| Original accuracy:            | 95.5%  |
| Accuracy under attack:        | 53.7%  |
| Attack success rate:          | 43.77% |
| Average perturbed word %:     | 21.07% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 282.27 |
+-------------------------------+--------+


### TextBugger
__TextBugger: Generating Adversarial Text Against Real-world Applications.__ <br>
Deep Learning-based Text Understanding (DLTU) is the backbone technique behind various applications, including question answering, machine translation, and text classification. Despite its tremendous popularity, the security vulnerabilities of DLTU are still largely unknown, which is highly concerning given its increasing use in security-sensitive applications such as sentiment analysis and toxic content detection. In this paper, we show that DLTU is inherently vulnerable to adversarial text attacks, in which maliciously crafted texts trigger target DLTU systems and services to misbehave. Specifically, we present TextBugger, a general attack framework for generating adversarial texts. In contrast to prior works, TextBugger differs in significant ways: (i) effective -- it outperforms state-of-the-art attacks in terms of attack success rate; (ii) evasive -- it preserves the utility of benign text, with 94.9\% of the adversarial text correctly recognized by human readers; and (iii) efficient -- it generates adversarial text with computational complexity sub-linear to the text length. We empirically evaluate TextBugger on a set of real-world DLTU systems and services used for sentiment analysis and toxic content detection, demonstrating its effectiveness, evasiveness, and efficiency. For instance, TextBugger achieves 100\% success rate on the IMDB dataset based on Amazon AWS Comprehend within 4.61 seconds and preserves 97\% semantic similarity. We further discuss possible defense mechanisms to mitigate such attack and the adversary's potential countermeasures, which leads to promising directions for further research.



In [82]:
attack_recipe.value= 'TextBuggerLi2018'
tf.print(f'****Attack Recipe:{attack_recipe.value}*****')
tf.print(f'****Query size:{query_budget.value}*****')
tf.print(f'****Number of examples:{num_examples.value}*****')

****Attack Recipe:TextBuggerLi2018*****
****Query size:6000*****
****Number of examples:1000*****


#### BERT

In [83]:
attack_model(bert, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/TextBuggerLi2018/BERT_nexp1000_qb6000_2021-12-06_02:59.csv

  0%|          | 0/1000 [00:00<?, ?it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  CompositeTransformation(
    (0): WordSwapRandomCharacterInsertion(
        (random_one):  True
      )
    (1): WordSwapRandomCharacterDeletion(
        (random_one):  True
      )
    (2): WordSwapNeighboringCharacterSwap(
        (random_one):  True
      )
    (3): WordSwapHomoglyphSwap
    (4): WordSwapEmbedding(
        (max_candidates):  5
        (embedding):  WordEmbedding
      )
    )
  (constraints): 
    (0): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8
        (window_size):  inf
        (skip_text_shorter_than_window):  False
        (compare_against_original):  True
      )
    (1): RepeatModification
    (2): StopwordModification
  (is_black_box):  True
) 




  0%|          | 1/1000 [00:04<1:09:48,  4.19s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 1/1000 [00:04<1:10:00,  4.20s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[1 (73%)]] --> [[0 (69%)]]

back in march former deputy prime minister barnabyjoyce said death by snake bite outnumbered covid death by a factor of to but coronavirus move quickly and his claim rapidly aged this and more in [[coronacheck]] [[coronavirusfacts]]

back in march former deputy prime minister barnabyjoyce said death by snake bite outnumbered covid death by a factor of to but coronavirus move quickly and his claim rapidly aged this and more in [[coronacհeck]] [[coronavirսsfacts]]





[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 2/1000 [00:06<58:11,  3.50s/it]  
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   0%|          | 2/1000 [00:07<58:16,  3.50s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[0 (73%)]] --> [[[FAILED]]]

looking at the case data there is now a fairly clear low plateau where the day average stayed between k case per day this extended from to so from ago to day ago





[Succeeded / Failed / Skipped / Total] 621 / 319 / 58 / 998: 100%|█████████▉| 999/1000 [18:03<00:01,  1.08s/it]
[Succeeded / Failed / Skipped / Total] 622 / 319 / 58 / 999: 100%|█████████▉| 999/1000 [18:03<00:01,  1.08s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (73%)]] --> [[1 (57%)]]

arizona [[put]] out a somewhat [[encouraging]] set of number unclear if this is the beginning of a real downward [[trend]] or just some bump on an upward trajectory

arizona [[putting]] out a somewhat [[encouⲅaging]] set of number unclear if this is the beginning of a real downward [[trenԁ]] or just some bump on an upward trajectory





[Succeeded / Failed / Skipped / Total] 622 / 319 / 58 / 999: 100%|██████████| 1000/1000 [18:04<00:00,  1.08s/it]
[Succeeded / Failed / Skipped / Total] 623 / 319 / 58 / 1000: 100%|██████████| 1000/1000 [18:04<00:00,  1.08s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[1 (73%)]] --> [[0 (60%)]]

the [[novel]] coronavirus ncov will not last long in the [[philippine]] because of it warm climate

the [[newest]] coronavirus ncov will not last long in the [[philippines]] because of it warm climate



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 623    |
| Number of failed attacks:     | 319    |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 94.2%  |
| Accuracy under attack:        | 31.9%  |
| Attack success rate:          | 66.14% |
| Average perturbed word %:     | 23.38% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 82.71  |
+-------------------------------+--------+


#### MT BERT

In [84]:
attack_model(bert_teacher, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             'MT'+model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/TextBuggerLi2018/MTBERT_nexp1000_qb6000_2021-12-06_03:17.csv

  0%|          | 0/1000 [00:00<?, ?it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  CompositeTransformation(
    (0): WordSwapRandomCharacterInsertion(
        (random_one):  True
      )
    (1): WordSwapRandomCharacterDeletion(
        (random_one):  True
      )
    (2): WordSwapNeighboringCharacterSwap(
        (random_one):  True
      )
    (3): WordSwapHomoglyphSwap
    (4): WordSwapEmbedding(
        (max_candidates):  5
        (embedding):  WordEmbedding
      )
    )
  (constraints): 
    (0): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8
        (window_size):  inf
        (skip_text_shorter_than_window):  False
        (compare_against_original):  True
      )
    (1): RepeatModification
    (2): StopwordModification
  (is_black_box):  True
) 




  0%|          | 1/1000 [00:04<1:10:48,  4.25s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 1/1000 [00:04<1:11:01,  4.27s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[1 (60%)]] --> [[0 (53%)]]

back in march former deputy prime minister barnabyjoyce said death by snake bite outnumbered covid death by a factor of to but coronavirus move quickly and his claim rapidly aged this and more in [[coronacheck]] [[coronavirusfacts]]

back in march former deputy prime minister barnabyjoyce said death by snake bite outnumbered covid death by a factor of to but coronavirus move quickly and his claim rapidly aged this and more in [[coronacհeck]] [[coⲅonavirusfacts]]





[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 2/1000 [00:07<1:03:51,  3.84s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   0%|          | 2/1000 [00:07<1:03:58,  3.85s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[0 (63%)]] --> [[[FAILED]]]

looking at the case data there is now a fairly clear low plateau where the day average stayed between k case per day this extended from to so from ago to day ago





[Succeeded / Failed / Skipped / Total] 294 / 659 / 45 / 998: 100%|█████████▉| 999/1000 [26:26<00:01,  1.59s/it]
[Succeeded / Failed / Skipped / Total] 295 / 659 / 45 / 999: 100%|█████████▉| 999/1000 [26:26<00:01,  1.59s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (61%)]] --> [[1 (53%)]]

arizona put out a somewhat [[encouraging]] set of [[number]] unclear if this is the [[beginning]] of a [[real]] downward [[trend]] or just some bump on an [[upward]] trajectory

arizona put out a somewhat [[heartening]] set of [[numbers]] unclear if this is the [[beg]] [[inning]] of a [[reales]] downward [[tred]] or just some bump on an [[ascendant]] trajectory





[Succeeded / Failed / Skipped / Total] 295 / 659 / 45 / 999: 100%|██████████| 1000/1000 [26:27<00:00,  1.59s/it]
[Succeeded / Failed / Skipped / Total] 295 / 660 / 45 / 1000: 100%|██████████| 1000/1000 [26:27<00:00,  1.59s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[1 (61%)]] --> [[[FAILED]]]

the novel coronavirus ncov will not last long in the philippine because of it warm climate



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 295    |
| Number of failed attacks:     | 660    |
| Number of skipped attacks:    | 45     |
| Original accuracy:            | 95.5%  |
| Accuracy under attack:        | 66.0%  |
| Attack success rate:          | 30.89% |
| Average perturbed word %:     | 23.61% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 114.14 |
+-------------------------------+--------+


### PWWS
__PWWSRen 2019 - Generating Natural Language Adversarial Examples through Probability Weighted Word Saliency. Shuhuai Ren, Yihe Deng, Kun He, Wanxiang Che__<br>
Based on the synonyms substitution strategy, they introduced a new word replacement order determined by both the word saliency and the classification probability, and propose a greedy algorithm called probability weighted word saliency (PWWS) for text adversarial attack.

In [85]:
attack_recipe.value= 'PWWSRen2019'

# because of issue in PWWS attack provided by textattack I need to change the number of  queries = number of examples
# query_budget.value = 6000
tf.print(f'****Attack Recipe:{attack_recipe.value}*****')
tf.print(f'****Query size:{query_budget.value}*****')
tf.print(f'****Number of examples:{num_examples.value}*****')

****Attack Recipe:PWWSRen2019*****
****Query size:6000*****
****Number of examples:1000*****


#### BERT

In [86]:
attack_model(bert, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/PWWSRen2019/BERT_nexp1000_qb6000_2021-12-06_03:44.csv

  0%|          | 0/1000 [00:00<?, ?it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  weighted-saliency
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapWordNet
  (constraints): 
    (0): RepeatModification
    (1): StopwordModification
  (is_black_box):  True
) 




  0%|          | 1/1000 [00:03<53:09,  3.19s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 1/1000 [00:03<53:20,  3.20s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[1 (73%)]] --> [[0 (61%)]]

back in march former deputy [[prime]] minister barnabyjoyce [[said]] death by snake bite outnumbered covid death by a factor of to but coronavirus move quickly and his [[claim]] rapidly aged this and more in coronacheck coronavirusfacts

back in march former deputy [[meridian]] minister barnabyjoyce [[enunciate]] death by snake bite outnumbered covid death by a factor of to but coronavirus move quickly and his [[title]] rapidly aged this and more in coronacheck coronavirusfacts





[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 2/1000 [00:10<1:24:31,  5.08s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   0%|          | 2/1000 [00:10<1:24:37,  5.09s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[0 (73%)]] --> [[1 (53%)]]

[[looking]] at the [[case]] data there is now a fairly clear low plateau where the day [[average]] stayed between [[k]] [[case]] per day this [[extended]] from to so from ago to day ago

[[reckon]] at the [[eccentric]] data there is now a fairly clear low plateau where the day [[ordinary]] stayed between [[kelvin]] [[pillowcase]] per day this [[strain]] from to so from ago to day ago





[Succeeded / Failed / Skipped / Total] 691 / 249 / 58 / 998: 100%|█████████▉| 999/1000 [45:15<00:02,  2.72s/it]
[Succeeded / Failed / Skipped / Total] 692 / 249 / 58 / 999: 100%|█████████▉| 999/1000 [45:15<00:02,  2.72s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (73%)]] --> [[1 (55%)]]

arizona put out a somewhat encouraging [[set]] of [[number]] unclear if this is the beginning of a real downward [[trend]] or just some bump on an upward trajectory

arizona put out a somewhat encouraging [[coiffe]] of [[numeral]] unclear if this is the beginning of a real downward [[curve]] or just some bump on an upward trajectory





[Succeeded / Failed / Skipped / Total] 692 / 249 / 58 / 999: 100%|██████████| 1000/1000 [45:16<00:00,  2.72s/it]
[Succeeded / Failed / Skipped / Total] 693 / 249 / 58 / 1000: 100%|██████████| 1000/1000 [45:16<00:00,  2.72s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[1 (73%)]] --> [[0 (51%)]]

the [[novel]] coronavirus ncov will not [[last]] [[long]] in the philippine because of it warm climate

the [[new]] coronavirus ncov will not [[conclusion]] [[recollective]] in the philippine because of it warm climate



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 693    |
| Number of failed attacks:     | 249    |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 94.2%  |
| Accuracy under attack:        | 24.9%  |
| Attack success rate:          | 73.57% |
| Average perturbed word %:     | 20.28% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 217.19 |
+-------------------------------+--------+


#### MT BERT

In [87]:
attack_model(bert_teacher, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             'MT'+model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/PWWSRen2019/MTBERT_nexp1000_qb6000_2021-12-06_04:29.csv

  0%|          | 0/1000 [00:00<?, ?it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  weighted-saliency
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapWordNet
  (constraints): 
    (0): RepeatModification
    (1): StopwordModification
  (is_black_box):  True
) 




  0%|          | 1/1000 [00:05<1:28:08,  5.29s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|          | 1/1000 [00:05<1:28:18,  5.30s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[1 (60%)]] --> [[[FAILED]]]

back in march former deputy prime minister barnabyjoyce said death by snake bite outnumbered covid death by a factor of to but coronavirus move quickly and his claim rapidly aged this and more in coronacheck coronavirusfacts





[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|          | 2/1000 [00:12<1:41:12,  6.08s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   0%|          | 2/1000 [00:12<1:41:17,  6.09s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[0 (63%)]] --> [[[FAILED]]]

looking at the case data there is now a fairly clear low plateau where the day average stayed between k case per day this extended from to so from ago to day ago





[Succeeded / Failed / Skipped / Total] 364 / 589 / 45 / 998: 100%|█████████▉| 999/1000 [51:45<00:03,  3.11s/it]
[Succeeded / Failed / Skipped / Total] 365 / 589 / 45 / 999: 100%|█████████▉| 999/1000 [51:45<00:03,  3.11s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (61%)]] --> [[1 (52%)]]

arizona put out a somewhat encouraging [[set]] of [[number]] unclear if this is the beginning of a real downward trend or just some bump on an upward trajectory

arizona put out a somewhat encouraging [[dress]] of [[numeral]] unclear if this is the beginning of a real downward trend or just some bump on an upward trajectory





[Succeeded / Failed / Skipped / Total] 365 / 589 / 45 / 999: 100%|██████████| 1000/1000 [51:47<00:00,  3.11s/it]
[Succeeded / Failed / Skipped / Total] 365 / 590 / 45 / 1000: 100%|██████████| 1000/1000 [51:47<00:00,  3.11s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[1 (61%)]] --> [[[FAILED]]]

the novel coronavirus ncov will not last long in the philippine because of it warm climate



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 365    |
| Number of failed attacks:     | 590    |
| Number of skipped attacks:    | 45     |
| Original accuracy:            | 95.5%  |
| Accuracy under attack:        | 59.0%  |
| Attack success rate:          | 38.22% |
| Average perturbed word %:     | 18.01% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 239.3  |
+-------------------------------+--------+


### BAE
__BAEGarg2019-BAE (BAE: BERT-Based Adversarial Examples)__ <br>
BAE, a black box attack for generating adversarial examples using contextual perturbations from a BERT masked language model. BAE replaces and inserts tokens in the original text by masking a portion of the text and leveraging the BERT-MLM to generate alternatives for the masked tokens. Through automatic and human evaluations, we show that BAE performs a stronger attack, in addition to generating adversarial examples with improved grammaticality and semantic coherence as compared to prior work.


In [88]:
attack_recipe.value= 'BAEGarg2019'
tf.print(f'****Attack Recipe:{attack_recipe.value}*****')
tf.print(f'****Query size:{query_budget.value}*****')
tf.print(f'****Number of examples:{num_examples.value}*****')

****Attack Recipe:BAEGarg2019*****
****Query size:6000*****
****Number of examples:1000*****


#### BERT

In [89]:
attack_model(bert, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/BAEGarg2019/BERT_nexp1000_qb6000_2021-12-06_05:21.csv

  0%|          | 0/1000 [00:00<?, ?it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapMaskedLM(
    (method):  bae
    (masked_lm_name):  BertForMaskedLM
    (max_length):  512
    (max_candidates):  50
    (min_confidence):  0.0
  )
  (constraints): 
    (0): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (1): UniversalSentenceEncoder(
        (metric):  cosine
        (threshold):  0.936338023
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  True
      )
    (2): RepeatModification
    (3): StopwordModification
  (is_black_box):  True
) 




  0%|          | 1/1000 [00:05<1:37:45,  5.87s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 1/1000 [00:05<1:37:55,  5.88s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[1 (73%)]] --> [[0 (56%)]]

back in march former deputy prime minister barnabyjoyce [[said]] [[death]] by snake bite outnumbered covid death by a factor of to but [[coronavirus]] move quickly and his claim rapidly aged this and more in [[coronacheck]] coronavirusfacts

back in march former deputy prime minister barnabyjoyce [[reported]] [[deaths]] by snake bite outnumbered covid death by a factor of to but [[more]] move quickly and his claim rapidly aged this and more in [[using]] coronavirusfacts





[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 2/1000 [00:09<1:21:34,  4.90s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   0%|          | 2/1000 [00:09<1:21:40,  4.91s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[0 (73%)]] --> [[[FAILED]]]

looking at the case data there is now a fairly clear low plateau where the day average stayed between k case per day this extended from to so from ago to day ago





[Succeeded / Failed / Skipped / Total] 266 / 674 / 58 / 998: 100%|█████████▉| 999/1000 [39:26<00:02,  2.37s/it]
[Succeeded / Failed / Skipped / Total] 266 / 675 / 58 / 999: 100%|█████████▉| 999/1000 [39:26<00:02,  2.37s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (73%)]] --> [[[FAILED]]]

arizona put out a somewhat encouraging set of number unclear if this is the beginning of a real downward trend or just some bump on an upward trajectory





[Succeeded / Failed / Skipped / Total] 266 / 675 / 58 / 999: 100%|██████████| 1000/1000 [39:27<00:00,  2.37s/it]
[Succeeded / Failed / Skipped / Total] 266 / 676 / 58 / 1000: 100%|██████████| 1000/1000 [39:27<00:00,  2.37s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[1 (73%)]] --> [[[FAILED]]]

the novel coronavirus ncov will not last long in the philippine because of it warm climate



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 266    |
| Number of failed attacks:     | 676    |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 94.2%  |
| Accuracy under attack:        | 67.6%  |
| Attack success rate:          | 28.24% |
| Average perturbed word %:     | 19.84% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 81.36  |
+-------------------------------+--------+


#### MT BERT

In [90]:
attack_model(bert_teacher, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             'MT'+model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/BAEGarg2019/MTBERT_nexp1000_qb6000_2021-12-06_06:01.csv

  0%|          | 0/1000 [00:00<?, ?it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapMaskedLM(
    (method):  bae
    (masked_lm_name):  BertForMaskedLM
    (max_length):  512
    (max_candidates):  50
    (min_confidence):  0.0
  )
  (constraints): 
    (0): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (1): UniversalSentenceEncoder(
        (metric):  cosine
        (threshold):  0.936338023
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  True
      )
    (2): RepeatModification
    (3): StopwordModification
  (is_black_box):  True
) 




  0%|          | 1/1000 [00:07<1:58:19,  7.11s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|          | 1/1000 [00:07<1:58:29,  7.12s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[1 (60%)]] --> [[[FAILED]]]

back in march former deputy prime minister barnabyjoyce said death by snake bite outnumbered covid death by a factor of to but coronavirus move quickly and his claim rapidly aged this and more in coronacheck coronavirusfacts





[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|          | 2/1000 [00:11<1:36:45,  5.82s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   0%|          | 2/1000 [00:11<1:36:50,  5.82s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[0 (63%)]] --> [[[FAILED]]]

looking at the case data there is now a fairly clear low plateau where the day average stayed between k case per day this extended from to so from ago to day ago





[Succeeded / Failed / Skipped / Total] 183 / 770 / 45 / 998: 100%|█████████▉| 999/1000 [41:27<00:02,  2.49s/it]
[Succeeded / Failed / Skipped / Total] 183 / 771 / 45 / 999: 100%|█████████▉| 999/1000 [41:27<00:02,  2.49s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (61%)]] --> [[[FAILED]]]

arizona put out a somewhat encouraging set of number unclear if this is the beginning of a real downward trend or just some bump on an upward trajectory





[Succeeded / Failed / Skipped / Total] 183 / 771 / 45 / 999: 100%|██████████| 1000/1000 [41:29<00:00,  2.49s/it]
[Succeeded / Failed / Skipped / Total] 183 / 772 / 45 / 1000: 100%|██████████| 1000/1000 [41:29<00:00,  2.49s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[1 (61%)]] --> [[[FAILED]]]

the novel coronavirus ncov will not last long in the philippine because of it warm climate



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 183    |
| Number of failed attacks:     | 772    |
| Number of skipped attacks:    | 45     |
| Original accuracy:            | 95.5%  |
| Accuracy under attack:        | 77.2%  |
| Attack success rate:          | 19.16% |
| Average perturbed word %:     | 16.38% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 88.84  |
+-------------------------------+--------+
